In [1]:
import re
import time
import requests

import pandas as pd
import yaml
from tqdm.auto import tqdm
from html_to_markdown import convert_to_markdown

from selenium import webdriver
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from selenium.webdriver.chrome.options import Options
from selenium.common.exceptions import TimeoutException, NoSuchElementException

tqdm.pandas()

from dotenv import load_dotenv

load_dotenv()


True

In [2]:
DOCS_SITEMAP_XML = "https://create.roblox.com/docs/sitemap.1.xml"
LUAU_NAV_YAML = "https://raw.githubusercontent.com/luau-lang/site/refs/heads/master/_data/navigation.yml"

DOCS_CONTENT_MAIN_ID = "main" # <main id="main">
LUAU_CONTENT_DIV_CLASS = "page__inner-wrap" # <div class="page__inner-wrap">


In [3]:
# Setup Selenium WebDriver with Chrome
def create_driver(headless=True):
    """Create and configure a Chrome WebDriver instance."""
    chrome_options = Options()
    if headless:
        chrome_options.add_argument("--headless")
    chrome_options.add_argument("--no-sandbox")
    chrome_options.add_argument("--disable-dev-shm-usage")
    chrome_options.add_argument("--disable-gpu")
    chrome_options.add_argument("--window-size=1920,1080")
    # Disable images to speed up loading
    chrome_options.add_argument("--blink-settings=imagesEnabled=false")

    driver = webdriver.Chrome(options=chrome_options)
    return driver

# Initialize the driver
driver = create_driver(headless=True)


Error sending stats to Plausible: error sending request for url (https://plausible.io/api/event)


In [4]:
# First, we gather all the URLs we plan to visit using regular requests
luau_nav_response = requests.get(LUAU_NAV_YAML)
luau_nav_response.raise_for_status()
luau_urls = []
for page in yaml.safe_load(luau_nav_response.text).get("pages", []):
    luau_urls.append(f"https://luau.org{page['url']}")

docs_sitemap_response = requests.get(DOCS_SITEMAP_XML)
docs_sitemap_response.raise_for_status()
docs_urls = []
for url in re.findall(r'<loc>(.*?)</loc>', docs_sitemap_response.text, re.DOTALL):
    docs_urls.append(url.strip())

print(luau_urls[:5])
print(docs_urls[:5])


['https://luau.org/getting-started', 'https://luau.org/why', 'https://luau.org/syntax', 'https://luau.org/lint', 'https://luau.org/performance']
['https://create.roblox.com/docs', 'https://create.roblox.com/docs/id-id/cloud', 'https://create.roblox.com/docs/id-id/education/educator-onboarding/landing', 'https://create.roblox.com/docs/id-id/production/promotion/content-maturity', 'https://create.roblox.com/docs/id-id/production/publishing/about-GDPR-and-CCPA']


In [5]:
df = pd.DataFrame(
    columns=[
        "url",
        "language",
        "content",
    ]
)


In [6]:
progress = tqdm(luau_urls, desc="Processing Luau URLs")
for url in progress:
    progress.set_postfix_str(url)

    try:
        # Navigate to the page
        driver.get(url)

        # Wait for the content to load
        wait = WebDriverWait(driver, 20)
        content_element = wait.until(
            EC.presence_of_element_located((By.CLASS_NAME, LUAU_CONTENT_DIV_CLASS))
        )

        # Additional wait to ensure dynamic content is loaded
        time.sleep(0.1)

        # Get the HTML content
        content_html = content_element.get_attribute('innerHTML')

        if content_html:
            content = convert_to_markdown(content_html, heading_style="atx")
            df.loc[len(df)] = [url, "en-us", content]
            tqdm.write(f"Processed {url}")
        else:
            tqdm.write(f"Failed to extract content from {url}")
            continue

    except TimeoutException:
        tqdm.write(f"Timeout while loading {url}")
    except NoSuchElementException:
        tqdm.write(f"Could not find content element on {url}")
    except Exception as e:
        tqdm.write(f"Error processing {url}: {e}")

progress.close()
df


Processing Luau URLs:   0%|          | 0/11 [00:00<?, ?it/s]

Processed https://luau.org/getting-started
Processed https://luau.org/why
Processed https://luau.org/syntax
Processed https://luau.org/lint
Processed https://luau.org/performance
Processed https://luau.org/sandbox
Processed https://luau.org/compatibility
Processed https://luau.org/typecheck
Processed https://luau.org/profile
Processed https://luau.org/library
Processed https://luau.org/grammar


url language  \
0   https://luau.org/getting-started    en-us   
1               https://luau.org/why    en-us   
2            https://luau.org/syntax    en-us   
3              https://luau.org/lint    en-us   
4       https://luau.org/performance    en-us   
5           https://luau.org/sandbox    en-us   
6     https://luau.org/compatibility    en-us   
7         https://luau.org/typecheck    en-us   
8           https://luau.org/profile    en-us   
9           https://luau.org/library    en-us   
10          https://luau.org/grammar    en-us   

                                              content  
0   \n# Getting Started\n\n#### On this page\n\n* ...  
1   \n# Why Luau?\n\nAround 2006, [Roblox](https:/...  
2   \n# Syntax\n\n#### On this page\n\n* [String l...  
3   \n# Linting\n\n#### On this page\n\n* [Unknown...  
4   \n# Performance\n\n#### On this page\n\n* [Fas...  
5   \n# Sandboxing\n\n#### On this page\n\n* [Libr...  
6   \n# Compatibility\n\n#### On this page\n\n* [I...  
7   \n# Type checking\n\n#### On this page\n\n* [T...  
8   \n# Profiling\n\n#### On this page\n\nOne of m...  
9   \n# Library\n\n#### On this page\n\n* [Global ...  
10  \n# Grammar\n\nThis is the complete syntax gra...

In [7]:
progress = tqdm(docs_urls, desc="Processing Docs URLs")
for url in progress:
    progress.set_postfix_str(url)

    try:
        # Navigate to the page
        driver.get(url)

        # Wait for the content to load
        wait = WebDriverWait(driver, 20)
        content_element = wait.until(
            EC.presence_of_element_located((By.ID, DOCS_CONTENT_MAIN_ID))
        )

        # Additional wait to ensure dynamic content is loaded
        time.sleep(0.15)

        # Get the HTML content
        content_html = content_element.get_attribute('innerHTML')

        if content_html:
            content = convert_to_markdown(content_html, heading_style="atx")

            # Extract language from url
            lang_match = re.search(r'/docs/([a-z]{2}-[a-z]{2})/', url)
            if lang_match:
                language = lang_match.group(1)
            else:
                language = "en-us"

            df.loc[len(df)] = [url, language, content]
            tqdm.write(f"Processed {url}")
        else:
            tqdm.write(f"Failed to extract content from {url}")
            continue

    except TimeoutException:
        tqdm.write(f"Timeout while loading {url}")
    except NoSuchElementException:
        tqdm.write(f"Could not find content element on {url}")
    except Exception as e:
        tqdm.write(f"Error processing {url}: {e}")

progress.close()
df


Processing Docs URLs:   0%|          | 0/19600 [00:00<?, ?it/s]

Processed https://create.roblox.com/docs
Processed https://create.roblox.com/docs/id-id/cloud
Processed https://create.roblox.com/docs/id-id/education/educator-onboarding/landing
Processed https://create.roblox.com/docs/id-id/production/promotion/content-maturity
Processed https://create.roblox.com/docs/id-id/production/publishing/about-GDPR-and-CCPA
Processed https://create.roblox.com/docs/id-id/production/publishing/dmca-guidelines
Processed https://create.roblox.com/docs/id-id/ai-data-sharing
Processed https://create.roblox.com/docs/id-id/production/publishing/account-verification
Processed https://create.roblox.com/docs/id-id/projects/group-guidelines
Processed https://create.roblox.com/docs/id-id/marketplace/marketplace-policy
Processed https://create.roblox.com/docs/id-id/marketplace/intellectual-property
Processed https://create.roblox.com/docs/id-id/marketplace/moderation
Processed https://create.roblox.com/docs/id-id/marketplace/frequently-asked-questions
Processed https://cre

url language  \
0                       https://luau.org/getting-started    en-us   
1                                   https://luau.org/why    en-us   
2                                https://luau.org/syntax    en-us   
3                                  https://luau.org/lint    en-us   
4                           https://luau.org/performance    en-us   
...                                                  ...      ...   
19605  https://create.roblox.com/docs/ko-kr/education...    ko-kr   
19606  https://create.roblox.com/docs/ko-kr/education...    ko-kr   
19607  https://create.roblox.com/docs/ko-kr/education...    ko-kr   
19608  https://create.roblox.com/docs/ko-kr/education...    ko-kr   
19609  https://create.roblox.com/docs/ko-kr/creator-p...    ko-kr   

                                                 content  
0      \n# Getting Started\n\n#### On this page\n\n* ...  
1      \n# Why Luau?\n\nAround 2006, [Roblox](https:/...  
2      \n# Syntax\n\n#### On this page\n\n* [String l...  
3      \n# Linting\n\n#### On this page\n\n* [Unknown...  
4      \n# Performance\n\n#### On this page\n\n* [Fas...  
...                                                  ...  
19605  1. [생성](/docs/ko-kr/platform)\n2. /\n3. [개요](/...  
19606  1. [생성](/docs/ko-kr/platform)\n2. /\n3. [개요](/...  
19607  1. [생성](/docs/ko-kr/platform)\n2. /\n3. [개요](/...  
19608  1. [생성](/docs/ko-kr/platform)\n2. /\n3. [개요](/...  
19609  1. [생성](/docs/ko-kr/platform)\n2. /\n3. [개요](/...  

[19610 rows x 3 columns]

In [8]:
print(f"Processed {len(df)} pages")
df.to_parquet("train.parquet")


Processed 19610 pages


In [9]:
# Clean up - close the driver
driver.quit()
